In [1]:
# Allows import from parent directory.
import sys; sys.path.append('..')

import os

import matplotlib.pyplot as plt
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
import src.visualization_utils as viz
from scipy.spatial.transform import Rotation
from src import utils
from src.loaders import DetectionsLoader, FrameLoader
from src.perspective import Perspective

pio.templates['tight'] = dict(
    layout=dict(
        margin=dict(l=10, r=10, t=10, b=10),
        font=dict(family='charter', color='black', size=14),
    )
)
pio.templates.default = 'plotly_white+tight'


In [2]:
frame_loader = FrameLoader('../data/videos/s110_south_video_frames')
detections_loader = DetectionsLoader('../data/detections/s110_south_video/coco_mask_rcnn_R_50_FPN_3x')

# Perspective for intersection
perspective = Perspective(
    Rotation.from_euler('YZX', angles=(180, 59 + 180, 90 - 19.464948281006), degrees=True)
    .as_matrix()
    .T,
    translation=np.array([[0, 0, 7]]).T,
    intrinsic_matrix=np.array(
        [
            [1400.3096617691212, 0.0, 967.7899705163408],
            [0.0, 1403.041082755918, 581.7195041357244],
            [0.0, 0.0, 1.0],
        ]
    ),
    image_shape=(1200, 1920)
)


output_dir = 'output/intersection'
os.makedirs(output_dir, exist_ok=True)

In [3]:
# Image from intersection

index = 845
frame = frame_loader.load_item(index)
detections = detections_loader.load_item(index)
detections = [d for d in detections if d.score > 0.5 and d.label in [2,5,7] and np.linalg.norm(d.mask.shape) > 80]

plt.imsave(os.path.join(output_dir, 'frame.jpg'), frame)

px.imshow(frame)

In [4]:
# Create improved contours and project them onto ground.


def correct_bottom_contour(
    points: np.ndarray, limit: float = 4, margin_factor: float = 1 / 5
) -> np.ndarray:
    """
    Cut off contour at the start and end margins
    if difference between y values is greater than limit.
    """

    num_points = points.shape[1]
    margin = int(num_points * margin_factor)

    # Calculate y difference greater than limits for start- and end regions.
    start = np.argwhere(np.abs(np.diff(points[1, :margin])) > limit)
    end = np.argwhere(np.abs(np.diff(points[1, num_points - margin :])) > limit)

    # Trim start- and end index to skip large y differences.
    a = start[-1, 0] + 1 if start.size else 0
    b = num_points - margin + end[0, 0] if end.size else num_points

    valid_points = points[:, a:b]

    return valid_points


ground_contours = []
image_contours = []
for detection in detections:
    image_contour = utils.calculate_bottom_contour(detection, anchored=False)
    image_contour = correct_bottom_contour(image_contour)
    image_contour = utils.interpolate_path(image_contour, n=32, smoothing=1)

    image_contours.append(image_contour)

    ground_contour = perspective.project_to_ground(image_contour)
    ground_contours.append(ground_contour)

In [5]:
# Contours on image

fig = px.imshow(frame)
viz.draw_contours(fig, image_contours ,marker_size=4)
fig.update_yaxes(scaleanchor='x')

fig.update_layout(
    showlegend=False,
    xaxis=dict(showline=False, zeroline=False, showgrid=False, showticklabels=False),
    yaxis=dict(showline=False, zeroline=False, showgrid=False, showticklabels=False),
)
fig.write_image(os.path.join(output_dir, 'contours.pdf'))
fig

In [6]:
# Contours on ground

fig = go.Figure()
viz.draw_camera_position(fig, perspective)
viz.draw_contours(fig, ground_contours, marker_size=6)
fig.update_yaxes(scaleanchor='x')

fig.update_layout(
    height=500,
    width=1000,
    showlegend=False,
    xaxis=dict(showline=False, zeroline=False, showgrid=False, showticklabels=False),
    yaxis=dict(showline=False, zeroline=False, showgrid=False, showticklabels=False),
)
fig.write_image(os.path.join(output_dir, 'ground_contours.pdf'))
fig